In [2]:
import os
import sqlite3
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import ipywidgets as widgets
from IPython.display import display, HTML

# For Optuna
import optuna
from optuna.visualization import (
    plot_contour,
    plot_edf,
    plot_intermediate_values,
    plot_optimization_history,
    plot_param_importances,
    plot_parallel_coordinate,
    plot_slice,
    plot_timeline
)

# Optionally enable plotly for JupyterLab
try:
    import plotly.io as pio
    pio.renderers.default = "jupyterlab"
except Exception as e:
    print(f"Warning: Could not configure plotly for JupyterLab: {e}")

# Set up aesthetics for plots
plt.style.use('seaborn-v0_8-whitegrid')
sns.set_context("notebook", font_scale=1.2)
plt.rcParams['figure.figsize'] = (12, 8)
plt.rcParams['figure.dpi'] = 100

# Configure pandas display
pd.set_option('display.max_columns', None)
pd.set_option('display.expand_frame_repr', False)

# Optuna logging settings - reduce verbosity
optuna.logging.set_verbosity(optuna.logging.WARNING)

# Paths and configuration
DB_PATH = '/user/taed7566/Forecasting/wind-forecasting/optuna/SQL/flasc_tactis.db'

# Connect to the SQLite database
conn = sqlite3.connect(DB_PATH)
print(f"Successfully connected to database at {DB_PATH}")

# Load study from database
study_name = None  # Will be populated after querying the database

# Get the study name from the database
cursor = conn.cursor()
try:
    cursor.execute("SELECT study_name FROM studies LIMIT 1")
    study_name = cursor.fetchone()[0]
    print(f"Found study: {study_name}")
except Exception as e:
    print(f"Could not fetch study name: {e}")
    
# Load the study
try:
    study = optuna.load_study(study_name=study_name, storage=f"sqlite:///{DB_PATH}")
    print(f"Successfully loaded study '{study_name}' with {len(study.trials)} trials")
    print(f"Best value achieved: {study.best_value}")
    print(f"Best parameters: {study.best_params}")
except Exception as e:
    print(f"Error loading study: {e}")

Successfully connected to database at /user/taed7566/Forecasting/wind-forecasting/optuna/SQL/flasc_tactis.db
Found study: tuning_tactis_tune_hb_4_3_farm_128BS_400trials
Successfully loaded study 'tuning_tactis_tune_hb_4_3_farm_128BS_400trials' with 321 trials
Best value achieved: -3081.6171875
Best parameters: {'context_length_factor': 4, 'encoder_type': 'temporal', 'marginal_embedding_dim_per_head': 256, 'marginal_num_heads': 2, 'marginal_num_layers': 2, 'flow_input_encoder_layers': 6, 'flow_series_embedding_dim': 8, 'copula_embedding_dim_per_head': 8, 'copula_num_heads': 4, 'copula_num_layers': 3, 'copula_input_encoder_layers': 4, 'copula_series_embedding_dim': 64, 'decoder_dsf_num_layers': 3, 'decoder_dsf_hidden_dim': 128, 'decoder_mlp_num_layers': 2, 'decoder_mlp_hidden_dim': 32, 'decoder_transformer_num_layers': 5, 'decoder_transformer_embedding_dim_per_head': 64, 'decoder_transformer_num_heads': 5, 'decoder_num_bins': 200, 'lr_stage1': 0.000239492693639108, 'lr_stage2': 0.0014153

In [3]:
# Basic information about the study
print(f"Study name: {study.study_name}")
print(f"Study direction: {'MINIMIZE' if study.direction == optuna.study.StudyDirection.MINIMIZE else 'MAXIMIZE'}")
print(f"Total number of trials: {len(study.trials)}")
print(f"Number of completed trials: {len(study.get_trials(states=[optuna.trial.TrialState.COMPLETE]))}")
print(f"Number of pruned trials: {len(study.get_trials(states=[optuna.trial.TrialState.PRUNED]))}")
print(f"Number of failed trials: {len(study.get_trials(states=[optuna.trial.TrialState.FAIL]))}")

# Display best trial details
best_trial = study.best_trial
print("\nBest Trial Information:")
print(f"  Value: {best_trial.value}")
print(f"  Trial number: {best_trial.number}")
print(f"  Parameters:")
for param_name, param_value in best_trial.params.items():
    print(f"    {param_name}: {param_value}")

# Check if the study has user attributes
if study.user_attrs:
    print("\nStudy User Attributes:")
    for key, value in study.user_attrs.items():
        print(f"  {key}: {value}")

# Extract parameter names to understand the hyperparameter space
param_names = list(best_trial.params.keys())
print(f"\nHyperparameter names: {param_names}")

# Get parameter importance if scikit-learn is available
try:
    importance = optuna.importance.get_param_importances(study)
    print("\nParameter importance:")
    for param_name, score in importance.items():
        print(f"  {param_name}: {score:.4f}")
except Exception as e:
    print(f"\nCould not calculate parameter importance: {e}")

Study name: tuning_tactis_tune_hb_4_3_farm_128BS_400trials
Study direction: MINIMIZE
Total number of trials: 321
Number of completed trials: 144
Number of pruned trials: 173
Number of failed trials: 0

Best Trial Information:
  Value: -3081.6171875
  Trial number: 308
  Parameters:
    context_length_factor: 4
    encoder_type: temporal
    marginal_embedding_dim_per_head: 256
    marginal_num_heads: 2
    marginal_num_layers: 2
    flow_input_encoder_layers: 6
    flow_series_embedding_dim: 8
    copula_embedding_dim_per_head: 8
    copula_num_heads: 4
    copula_num_layers: 3
    copula_input_encoder_layers: 4
    copula_series_embedding_dim: 64
    decoder_dsf_num_layers: 3
    decoder_dsf_hidden_dim: 128
    decoder_mlp_num_layers: 2
    decoder_mlp_hidden_dim: 32
    decoder_transformer_num_layers: 5
    decoder_transformer_embedding_dim_per_head: 64
    decoder_transformer_num_heads: 5
    decoder_num_bins: 200
    lr_stage1: 0.000239492693639108
    lr_stage2: 0.0014153115740382

In [4]:
# Convert trials to DataFrame for easier analysis
def trials_to_df(study):
    """Convert Optuna study trials to a pandas DataFrame."""
    # Extract trial data
    trials_data = []
    for trial in study.trials:
        if trial.state == optuna.trial.TrialState.COMPLETE:
            trial_dict = {
                'number': trial.number,
                'value': trial.value,
                'datetime_start': trial.datetime_start,
                'datetime_complete': trial.datetime_complete,
                'duration': (trial.datetime_complete - trial.datetime_start).total_seconds()
            }
            
            # Add parameters
            trial_dict.update(trial.params)
            
            # Add user attributes
            for key, value in trial.user_attrs.items():
                trial_dict[f"user_attr_{key}"] = value
            
            trials_data.append(trial_dict)
    
    # Create DataFrame
    df = pd.DataFrame(trials_data)
    
    # Sort by trial number
    df = df.sort_values('number')
    
    return df

# Create DataFrame
trials_df = trials_to_df(study)

# Display basic information about the DataFrame
print(f"DataFrame shape: {trials_df.shape}")
print("\nColumns:")
for col in trials_df.columns:
    print(f"  {col}")

# Display first few rows
print("\nFirst 5 rows:")
display(trials_df.head())

# Display basic statistics
print("\nBasic statistics for objective value:")
display(trials_df['value'].describe())

# Display statistics for each hyperparameter
print("\nHyperparameter statistics:")
param_cols = [col for col in trials_df.columns if col not in ['number', 'value', 'datetime_start', 'datetime_complete', 'duration'] 
              and not col.startswith('user_attr_')]
display(trials_df[param_cols].describe())

# Save DataFrame for later use
trials_df.to_csv('optuna_trials.csv', index=False)
print("\nSaved trials data to 'optuna_trials.csv'")

DataFrame shape: (144, 32)

Columns:
  number
  value
  datetime_start
  datetime_complete
  duration
  context_length_factor
  encoder_type
  marginal_embedding_dim_per_head
  marginal_num_heads
  marginal_num_layers
  flow_input_encoder_layers
  flow_series_embedding_dim
  copula_embedding_dim_per_head
  copula_num_heads
  copula_num_layers
  copula_input_encoder_layers
  copula_series_embedding_dim
  decoder_dsf_num_layers
  decoder_dsf_hidden_dim
  decoder_mlp_num_layers
  decoder_mlp_hidden_dim
  decoder_transformer_num_layers
  decoder_transformer_embedding_dim_per_head
  decoder_transformer_num_heads
  decoder_num_bins
  lr_stage1
  lr_stage2
  weight_decay_stage1
  weight_decay_stage2
  dropout_rate
  gradient_clip_val_stage1
  gradient_clip_val_stage2

First 5 rows:


number        value             datetime_start          datetime_complete     duration  context_length_factor encoder_type  marginal_embedding_dim_per_head  marginal_num_heads  marginal_num_layers  flow_input_encoder_layers  flow_series_embedding_dim  copula_embedding_dim_per_head  copula_num_heads  copula_num_layers  copula_input_encoder_layers  copula_series_embedding_dim  decoder_dsf_num_layers  decoder_dsf_hidden_dim  decoder_mlp_num_layers  decoder_mlp_hidden_dim  decoder_transformer_num_layers  decoder_transformer_embedding_dim_per_head  decoder_transformer_num_heads  decoder_num_bins  lr_stage1  lr_stage2  weight_decay_stage1  weight_decay_stage2  dropout_rate  gradient_clip_val_stage1  gradient_clip_val_stage2
0       1 -2026.978394 2025-04-25 23:28:35.302777 2025-04-26 00:11:18.153762  2562.850985                      3     temporal                              256                   3                    2                          4                         16                             16                 5                  4                            3                           32                       3                      64                       2                      64                               3                                          16                              3                50   0.000249   0.000685              0.00000              0.00100      0.145673                       0.0                       0.0
1       2 -1179.029297 2025-04-25 23:28:37.508217 2025-04-26 00:14:23.165706  2745.657489                      2     standard                               64                   2                    5                          6                          5                            128                 5                  3                            4                           16                       3                     512                       3                      48                               3                                         256                              5                50   0.000154   0.000510              0.00010              0.00000      0.111038                   10000.0                       0.0
2       3  -581.844971 2025-04-25 23:28:39.837268 2025-04-26 00:06:31.849125  2272.011857                      2     standard                               64                   3                    5                          4                        256                             64                 3                  3                            2                           32                       1                      64                       5                      16                               3                                         128                              7                50   0.000131   0.000770              0.00001              0.00100      0.063789                       0.0                       0.0
3       9  -415.010223 2025-04-26 00:11:18.175319 2025-04-26 00:51:10.473920  2392.298601                      1     temporal                              128                   2                    3                          4                          5                              8                 5                  4                            2                           16                       4                     512                       2                     128                               2                                         256                              5                20   0.000127   0.000745              0.00001              0.00000      0.182792                       0.0                    1000.0
4      10 -1005.497620 2025-04-26 00:14:23.188720 2025-04-26 00:50:35.207606  2172.018886                      2     temporal                                8                   6                    4                          4                         32                             16                 5                  4                           


Basic statistics for objective value:


count     144.000000
mean    -2275.740285
std       876.117795
min     -3081.617188
25%     -2788.067017
50%     -2675.668335
75%     -2080.403687
max       789.631836
Name: value, dtype: float64


Hyperparameter statistics:


context_length_factor  marginal_embedding_dim_per_head  marginal_num_heads  marginal_num_layers  flow_input_encoder_layers  flow_series_embedding_dim  copula_embedding_dim_per_head  copula_num_heads  copula_num_layers  copula_input_encoder_layers  copula_series_embedding_dim  decoder_dsf_num_layers  decoder_dsf_hidden_dim  decoder_mlp_num_layers  decoder_mlp_hidden_dim  decoder_transformer_num_layers  decoder_transformer_embedding_dim_per_head  decoder_transformer_num_heads  decoder_num_bins   lr_stage1   lr_stage2  weight_decay_stage1  weight_decay_stage2  dropout_rate  gradient_clip_val_stage1  gradient_clip_val_stage2
count             144.000000                       144.000000          144.000000           144.000000                 144.000000                 144.000000                     144.000000        144.000000         144.000000                   144.000000                   144.000000              144.000000              144.000000              144.000000              144.000000                      144.000000                                  144.000000                     144.000000        144.000000  144.000000  144.000000           144.000000           144.000000    144.000000                144.000000                144.000000
mean                3.722222                       215.444444            2.236111             2.166667                   5.895833                  18.270833                      42.055556          4.152778           2.951389                     3.743056                    59.111111                2.958333              185.000000                2.361111               68.777778                        3.972222                                   67.666667                       6.145833        144.583333    0.000303    0.001429             0.000086             0.000109      0.098011                756.944444               1138.888889
std                 0.704078                        82.308798            0.689442             0.603023                   0.622635                  42.594563                      65.675594          0.712716           0.492317                     0.634074                    34.750481                0.352315              174.510865                0.734857               70.357771                        1.348112                                   52.921369                       1.228842         70.272944    0.000217    0.000914             0.000211             0.000305      0.098653               2545.382568               3046.518387
min                 1.000000                         8.000000            2.000000             2.000000                   3.000000                   5.000000                       8.000000          2.000000           1.000000                     1.000000                    16.000000                1.000000               48.000000                2.000000                8.000000                        2.000000                                    8.000000                       3.000000         20.000000    0.000110    0.000114             0.000000             0.000000      0.000037                  0.000000                  0.000000
25%                 4.000000                       256.000000            2.000000             2.000000                   6.000000                   5.000000                       8.000000          4.000000           3.000000                     4.000000                    32.000000                3.000000               64.000000                2.000000               32.000000                        2.000000                                   48.000000                       6.000000        100.000000    0.000210    0.000472             0.000010             0.000000      0.017227                  0.000000                  0.000000
50%                 4.000000                       256.000000            2.000000             2.000000                   6.000000                   8.000000                       8.000000    


Saved trials data to 'optuna_trials.csv'


In [5]:
# Visualization using Optuna's built-in tools

# 1. Optimization History
print("## Optimization History")
print("Shows the history of the optimization process, plotting the objective value over trial numbers.")
fig = plot_optimization_history(study)
fig.update_layout(
    title="Optimization History",
    xaxis_title="Trial Number",
    yaxis_title="Objective Value",
    width=1000,
    height=600
)
fig.show()

# 2. Parameter Importances
print("\n## Parameter Importances")
print("Shows the relative importance of each hyperparameter in influencing the objective.")
try:
    fig = plot_param_importances(study)
    fig.update_layout(
        title="Parameter Importances",
        xaxis_title="Importance",
        yaxis_title="Parameter",
        width=1000,
        height=600
    )
    fig.show()
except Exception as e:
    print(f"Could not plot parameter importances: {e}")

# 3. Parallel Coordinate Plot
print("\n## Parallel Coordinate Plot")
print("Shows the relationship between hyperparameter values and objective value.")
fig = plot_parallel_coordinate(study)
fig.update_layout(
    title="Parallel Coordinate Plot",
    width=1200,
    height=700
)
fig.show()

# 4. Contour Plot
print("\n## Contour Plot")
print("Shows the relationship between pairs of hyperparameters and their impact on the objective.")
try:
    fig = plot_contour(study)
    fig.update_layout(
        title="Contour Plot",
        width=1200,
        height=800
    )
    fig.show()
except Exception as e:
    print(f"Could not create contour plot: {e}")

# 5. Slice Plot
print("\n## Slice Plot")
print("Shows the objective value as a function of each hyperparameter, while fixing others to their optimal values.")
fig = plot_slice(study)
fig.update_layout(
    title="Slice Plot",
    width=1200,
    height=800
)
fig.show()

# 6. EDF (Empirical Distribution Function) Plot
print("\n## EDF Plot")
print("Shows the empirical distribution of the objective values.")
fig = plot_edf(study)
fig.update_layout(
    title="Empirical Distribution Function of Objective Values",
    xaxis_title="Objective Value",
    yaxis_title="Cumulative Probability",
    width=1000,
    height=600
)
fig.show()

# 7. Timeline
print("\n## Trial Timeline")
print("Shows the execution timeline of the trials.")
try:
    # This plot requires trial start/completion times
    fig = plot_timeline(study)
    fig.update_layout(
        title="Trial Timeline",
        width=1200,
        height=600
    )
    fig.show()
except Exception as e:
    print(f"Could not create timeline plot: {e}")

## Optimization History
Shows the history of the optimization process, plotting the objective value over trial numbers.



## Parameter Importances
Shows the relative importance of each hyperparameter in influencing the objective.



## Parallel Coordinate Plot
Shows the relationship between hyperparameter values and objective value.



## Contour Plot
Shows the relationship between pairs of hyperparameters and their impact on the objective.



## Slice Plot
Shows the objective value as a function of each hyperparameter, while fixing others to their optimal values.



## EDF Plot
Shows the empirical distribution of the objective values.



## Trial Timeline
Shows the execution timeline of the trials.
